In [1]:
import pandas as pd
import geopandas as gpd
import shapely
import folium
from re import sub
from tqdm.auto import tqdm

In [2]:
layer_3 = gpd.read_file('data/la_layer3 (4).geojson')
#layer_3.loc[layer_3['Display Name'].isin(['Paradise Cove', 'Point Dume']), 'LAYER_3_PARENT_PID'] = '93731'
layer_3.head()

Display Name                Key  Selectable   PID LAYER_3_PARENT_PID  \
0    Adams Hill    adams_hill_1187        True  1187              93737   
1     Brockmont     brockmont_1188        True  1188              93737   
2   Chevy Chase   chevy_chase_1189        True  1189              93737   
3  Citrus Grove  citrus_grove_1190        True  1190              93737   
4   City Center   city_center_1191        True  1191              93737   

   Layer Name                                           geometry  
0           3  MULTIPOLYGON (((-118.23777 34.13522, -118.2377...  
1           3  MULTIPOLYGON (((-118.24348 34.17932, -118.2434...  
2           3  MULTIPOLYGON (((-118.19649 34.17991, -118.1964...  
3           3  MULTIPOLYGON (((-118.2288 34.14383, -118.22877...  
4           3  MULTIPOLYGON (((-118.25266 34.15679, -118.2526...

In [3]:
layer_2 = gpd.read_file('data/la_layer2.geojson')
layer_2.columns = ['PID', 'Display Name', 'Selectable', 'Key', 'LAYER_3_PARENT_PID', 'geometry']
layer_2['Layer Name'] = [2] * len(layer_2)
layer_2.head()

PID           Display Name  Selectable                          Key  \
0  93090  South Antelope Valley        True  south_antelope_valley_93090   
1  91750            Los Angeles        True            los_angeles_91750   
2  92110                Newhall        True                newhall_92110   
3  92360           Palos Verdes        True           palos_verdes_92360   
4  92785    San Fernando Valley        True    san_fernando_valley_92785   

   LAYER_3_PARENT_PID                                           geometry  \
0                   1  MULTIPOLYGON (((-118.41935 34.45567, -118.4193...   
1                   1  MULTIPOLYGON (((-118.50448 34.1279, -118.50443...   
2                   1  MULTIPOLYGON (((-118.81349 34.66051, -118.8081...   
3                   1  MULTIPOLYGON (((-118.41947 33.78551, -118.4191...   
4                   1  MULTIPOLYGON (((-118.66818 34.17926, -118.6681...   

   Layer Name  
0           2  
1           2  
2           2  
3           2  
4           2

In [4]:
#layer_2[layer_2['PID'] == '93731'].sjoin(layer_3, predicate='covered_by')

In [5]:
# add demotes
to_demote = ['Pomona','Arcadia','Monrovia','San Gabriel','Temple City','Alhambra','Hawthorne','North Hollywood','West Covina','La Verne','Claremont','Manhattan Beach','Redondo Beach','Topanga','Culver City']
precisely_all = precisely_all = gpd.read_file('data/NEIGHBORHOOD_BOUNDARIES_USA_202405_SHP/data', layer='neighborhood_objects_usa')\
    .merge(gpd.read_file('data/NEIGHBORHOOD_BOUNDARIES_USA_202405_SHP/data', layer='neighborhood_census_usa'), on='OBJ_ID')
macros_layer3 = precisely_all[(precisely_all['COUNTYFIPS'] == '06037') & (precisely_all['OBJ_SUBTYP'].str.contains('Macro')) & (precisely_all['OBJ_NAME'].isin(to_demote))]
overlaps = macros_layer3.sjoin(layer_3, predicate='covers')[['OBJ_ID', 'OBJ_NAME', 'PID', 'Display Name', 'geometry']]
overlaps

OBJ_ID     OBJ_NAME      PID                      Display Name  \
9803     20293       Pomona    66049                   Downtown Pomona   
9803     20293       Pomona  1239550  Wilton Heights Historic District   
9803     20293       Pomona  1239551    Lincoln Park Historic District   
9803     20293       Pomona  1239549   Hacienda Park Historic District   
10008    20579      Arcadia  1279072               Santa Anita Village   
...        ...          ...      ...                               ...   
40923  1146566  Culver City    10977                         Clarkdale   
40923  1146566  Culver City    10974                         Jefferson   
40923  1146566  Culver City    10975                         Park East   
40923  1146566  Culver City    10973                 Washington Culver   
40923  1146566  Culver City    10972                   Lucerne-Higuera   

                                                geometry  
9803   POLYGON ((-117.74894 34.11261, -117.74873 34.1...  
9803   POLYGON ((-117.74894 34.11261, -117.74873 34.1...  
9803   POLYGON ((-117.74894 34.11261, -117.74873 34.1...  
9803   POLYGON ((-117.74894 34.11261, -117.74873 34.1...  
10008  POLYGON ((-118.01826 34.17937, -118.018 34.179...  
...                                                  ...  
40923  POLYGON ((-118.38533 34.02752, -118.38502 34.0...  
40923  POLYGON ((-118.38533 34.02752, -118.38502 34.0...  
40923  POLYGON ((-118.38533 34.02752, -118.38502 34.0...  
40923  POLYGON ((-118.38533 34.02752, -118.38502 34.0...  
40923  POLYGON ((-118.38533 34.02752, -118.38502 34.0...  

[125 rows x 5 columns]

In [6]:
macros_layer3[macros_layer3['OBJ_NAME'] == 'Topanga'].sjoin(layer_2, predicate='overlaps')

OBJ_ID OBJ_NAME       OBJ_TYP OBJ_SUBTCD          OBJ_SUBTYP COUNTRY  \
40907  1146550  Topanga  Neighborhood          M  Macro Neighborhood     USA   
40907  1146550  Topanga  Neighborhood          M  Macro Neighborhood     USA   
40907  1146550  Topanga  Neighborhood          M  Macro Neighborhood     USA   
40907  1146550  Topanga  Neighborhood          M  Macro Neighborhood     USA   

                 METRO        LAT         LON   RELDATE  ...  MCDFIPS  \
40907  Los Angeles, CA  34.097566 -118.606137  20240404  ...    90015   
40907  Los Angeles, CA  34.097566 -118.606137  20240404  ...    90015   
40907  Los Angeles, CA  34.097566 -118.606137  20240404  ...    90015   
40907  Los Angeles, CA  34.097566 -118.606137  20240404  ...    90015   

         PLACE PLACEFIPS index_right    PID         Display Name Selectable  \
40907  Topanga   0678960           1  91750          Los Angeles       True   
40907  Topanga   0678960          20  93731               Malibu       True   
40907  Topanga   0678960           6  90015  Agoura Hills-Malibu       True   
40907  Topanga   0678960           4  92785  San Fernando Valley       True   

                             Key LAYER_3_PARENT_PID Layer Name  
40907          los_angeles_91750                  1          2  
40907            malibu_02378254                  1          2  
40907  agoura_hills_malibu_90015                  1          2  
40907  san_fernando_valley_92785                  1          2  

[4 rows x 30 columns]

In [7]:
geos_to_add = [x for x in to_demote if not x in overlaps['OBJ_NAME'].values]
parent_ids = ['90015']
# add demotions
count = 0
geo_name = []
geos = []
pid = []
key = []
max_pid = layer_3['PID'].astype(int).max() + 1
parent_key = []
for parent_name, parent_id in zip(geos_to_add, parent_ids):
    shape = macros_layer3[macros_layer3['OBJ_NAME'] == parent_name]['geometry'].values[0]
    #if not shapely.is_empty(exclude):
    #if not shapely.equals(all_childs, layer2[layer2['PID'] == parent_id]['geometry'].values[0]):
    #if shapely.is_empty(shapely.difference(all_childs, layer2[layer2['PID'] == parent_id]['geometry'].values[0])):
    geo_name.append(parent_name)
    geos.append(shape)
    pid.append(max_pid)
    max_pid += 1
    k = '_'.join(
            sub('([A-Z][a-z]+)', r' \1',
            sub('([A-Z]+)', r' \1',
            parent_name.replace('-', ' '))).split()) + '_' + str(max_pid)
    key.append(k)
    parent_key.append(parent_id)

add_to_layer3 = pd.DataFrame({'PID': pid,
                             'Display Name': geo_name,
                             'geometry': geos, 
                             'Selectable': [False]*len(geo_name),
                             'Key':key,
                             'Layer Name': [3] * len(geo_name),
                             'LAYER_3_PARENT_PID': parent_key})
layer_3 = pd.concat([layer_3, gpd.GeoDataFrame(add_to_layer3, crs='EPSG:4326')], ignore_index=True)

In [8]:
changed_shape = []
removed_shapes = []
for new_shape, old_shape in zip(overlaps['OBJ_NAME'], overlaps['PID']):
    if not new_shape in changed_shape:
        layer_3.loc[layer_3['PID'] == old_shape, 'geometry'] = macros_layer3[macros_layer3['OBJ_NAME'] == new_shape]['geometry'].values[0]
        layer_3.loc[layer_3['PID'] == old_shape, 'Key'] = '_'.join(
            sub('([A-Z][a-z]+)', r' \1',
            sub('([A-Z]+)', r' \1',
            new_shape.replace('-', ' '))).split()) + '_' + str(old_shape)
        layer_3.loc[layer_3['PID'] == old_shape, 'Display Name'] = new_shape
        changed_shape.append(new_shape)
    else:
        # print(f'dropping {old_shape}')
        #removed_shapes['name'].append(old_shape)
        removed_shapes.append(layer_3[layer_3['PID'] == old_shape])
        layer_3.drop(layer_3[layer_3['PID'] == old_shape].index, inplace=True)

print(changed_shape)
print(len(removed_shapes))

['Pomona', 'Arcadia', 'Monrovia', 'San Gabriel', 'Temple City', 'Alhambra', 'Hawthorne', 'North Hollywood', 'West Covina', 'La Verne', 'Claremont', 'Manhattan Beach', 'Redondo Beach', 'Culver City']
111


In [9]:
# TODO: parent_id check
layer_3.head()

Display Name                Key  Selectable   PID LAYER_3_PARENT_PID  \
0    Adams Hill    adams_hill_1187        True  1187              93737   
1     Brockmont     brockmont_1188        True  1188              93737   
2   Chevy Chase   chevy_chase_1189        True  1189              93737   
3  Citrus Grove  citrus_grove_1190        True  1190              93737   
4   City Center   city_center_1191        True  1191              93737   

   Layer Name                                           geometry  
0           3  MULTIPOLYGON (((-118.23777 34.13522, -118.2377...  
1           3  MULTIPOLYGON (((-118.24348 34.17932, -118.2434...  
2           3  MULTIPOLYGON (((-118.19649 34.17991, -118.1964...  
3           3  MULTIPOLYGON (((-118.2288 34.14383, -118.22877...  
4           3  MULTIPOLYGON (((-118.25266 34.15679, -118.2526...

In [10]:
layer_2.head()

PID           Display Name  Selectable                          Key  \
0  93090  South Antelope Valley        True  south_antelope_valley_93090   
1  91750            Los Angeles        True            los_angeles_91750   
2  92110                Newhall        True                newhall_92110   
3  92360           Palos Verdes        True           palos_verdes_92360   
4  92785    San Fernando Valley        True    san_fernando_valley_92785   

   LAYER_3_PARENT_PID                                           geometry  \
0                   1  MULTIPOLYGON (((-118.41935 34.45567, -118.4193...   
1                   1  MULTIPOLYGON (((-118.50448 34.1279, -118.50443...   
2                   1  MULTIPOLYGON (((-118.81349 34.66051, -118.8081...   
3                   1  MULTIPOLYGON (((-118.41947 33.78551, -118.4191...   
4                   1  MULTIPOLYGON (((-118.66818 34.17926, -118.6681...   

   Layer Name  
0           2  
1           2  
2           2  
3           2  
4           2

In [11]:
parent_check = layer_3.sjoin(layer_2, predicate='within')
parents_to_fix = parent_check[parent_check['LAYER_3_PARENT_PID_left'] != parent_check['PID_right']]
for child_id, parent_id in zip(parents_to_fix['PID_left'], parents_to_fix['PID_right']):
    layer_3.loc[layer_3['PID'] == child_id, 'LAYER_3_PARENT_PID'] = parent_id
parents_to_fix

Empty GeoDataFrame
Columns: [Display Name_left, Key_left, Selectable_left, PID_left, LAYER_3_PARENT_PID_left, Layer Name_left, geometry, index_right, PID_right, Display Name_right, Selectable_right, Key_right, LAYER_3_PARENT_PID_right, Layer Name_right]
Index: []

In [12]:
#overlap_check = layer_3.sjoin(layer_2, predicate='overlaps')
#overlap_correct = overlap_check[overlap_check['LAYER_3_PARENT_PID_left'] == parent_check['PID_right']]
#overlap_incorrect = overlap_check[overlap_check['LAYER_3_PARENT_PID_left'] != parent_check['PID_right']]
#only_in_incorrect = overlap_correct[~overlap_correct['PID_left'].isin(overlap_incorrect['PID_'])]

In [13]:
parents_to_change = parent_check[parent_check['LAYER_3_PARENT_PID_left'] != parent_check['PID_right']]
parents_to_change.head()
#for key, parent_id in zip(parents_to_change['Key_left'], parents_to_change[''])

Empty GeoDataFrame
Columns: [Display Name_left, Key_left, Selectable_left, PID_left, LAYER_3_PARENT_PID_left, Layer Name_left, geometry, index_right, PID_right, Display Name_right, Selectable_right, Key_right, LAYER_3_PARENT_PID_right, Layer Name_right]
Index: []

In [14]:
# fit layer 2 to layer 3
overlaps = layer_3.sjoin(layer_2, predicate='overlaps').reset_index(drop=True)[['PID_left', 'Display Name_left', 'LAYER_3_PARENT_PID_left', 'PID_right']]
overlaps.columns = ['PID_child', 'name_child', 'parent_id_child', 'PID_parent']
overlaps_correct = overlaps[(overlaps['parent_id_child'] == overlaps['PID_parent'])]
messed_up_layer3 = []
messed_up_layer2 = []
for layer3_id, layer2_id in zip(overlaps_correct['PID_child'], overlaps_correct['PID_parent']):
    real_parent_geo = layer_2[layer_2['PID'] == layer2_id]['geometry'].values[0]
    child = layer_3[layer_3['PID'] == layer3_id]['geometry'].values[0]
    try:
        layer_2.loc[layer_2['PID']==layer2_id,'geometry'] = shapely.union(real_parent_geo, shapely.difference(child, real_parent_geo))
    except:
        print(layer2_id, layer3_id)
        messed_up_layer2.append(layer2_id)
        messed_up_layer3.append(layer3_id)

/Users/arnavmalhotra/anaconda3/envs/pw_3.12/lib/python3.12/site-packages/shapely/set_operations.py:334: RuntimeWarning: invalid value encountered in union
  return lib.union(a, b, **kwargs)
/Users/arnavmalhotra/anaconda3/envs/pw_3.12/lib/python3.12/site-packages/shapely/set_operations.py:334: RuntimeWarning: invalid value encountered in union
  return lib.union(a, b, **kwargs)
/Users/arnavmalhotra/anaconda3/envs/pw_3.12/lib/python3.12/site-packages/shapely/set_operations.py:334: RuntimeWarning: invalid value encountered in union
  return lib.union(a, b, **kwargs)
/Users/arnavmalhotra/anaconda3/envs/pw_3.12/lib/python3.12/site-packages/shapely/set_operations.py:334: RuntimeWarning: invalid value encountered in union
  return lib.union(a, b, **kwargs)
/Users/arnavmalhotra/anaconda3/envs/pw_3.12/lib/python3.12/site-packages/shapely/set_operations.py:334: RuntimeWarning: invalid value encountered in union
  return lib.union(a, b, **kwargs)
/Users/arnavmalhotra/anaconda3/envs/pw_3.12/lib/py

In [15]:
overlaps_incorrect = overlaps[(overlaps['parent_id_child'] != overlaps['PID_parent'])]
for layer3_id, layer2_id in zip(overlaps_incorrect['PID_child'], overlaps_incorrect['PID_parent']):
    #if int(layer2_id) == 93731:
     #   continue
    geo_to_change = layer_2[layer_2['PID'] == layer2_id]['geometry'].values[0]
    child = layer_3[layer_3['PID'] == layer3_id]['geometry'].values[0]
    try:
        layer_2.loc[layer_2['PID']==layer2_id,'geometry'] = shapely.difference(geo_to_change, child)
    except:
        print(layer2_id, layer3_id)

In [16]:
wrong_type = []
for g, id in zip(layer_2.geometry, layer_2['PID']):
    if type(g) == shapely.GeometryCollection:
        wrong_type.append(id)
for id in wrong_type:
    poly = []
    for g in layer_2.loc[layer_2['PID'] == id, 'geometry'].values[0].geoms:
        if type(g) == shapely.geometry.Polygon:
            poly.append(g)
    layer_2.loc[layer_2['PID'] == id, 'geometry'] = shapely.MultiPolygon(poly)
wrong_type

['92785', '93737']

In [17]:
# add excludes
count = 0
geo_name = []
geos = []
pid = []
key = []
max_pid = layer_3['PID'].astype(int).max() + 1
parent_key = []
for parent_id in layer_2['PID']:
    all_childs = shapely.union_all(layer_3[layer_3['LAYER_3_PARENT_PID'] == parent_id]['geometry'].values)
    exclude = layer_2[layer_2['PID'] == parent_id]['geometry'].values[0].difference(all_childs)
    #if not shapely.is_empty(exclude):
    #if not shapely.equals(all_childs, layer2[layer2['PID'] == parent_id]['geometry'].values[0]):
    #if shapely.is_empty(shapely.difference(all_childs, layer2[layer2['PID'] == parent_id]['geometry'].values[0])):
    n = layer_2[layer_2['PID'] == parent_id]['Display Name'].values[0] + ' Exclude'
    geo_name.append(n)
    geos.append(exclude)
    pid.append(max_pid)
    max_pid += 1
    k = '_'.join(
            sub('([A-Z][a-z]+)', r' \1',
            sub('([A-Z]+)', r' \1',
            n.replace('-', ' '))).split()) + '_' + str(max_pid)
    key.append(k)
    parent_key.append(parent_id)

exclude_geos = pd.DataFrame({'PID': pid,
                             'Display Name': geo_name,
                             'geometry': geos, 
                             'Selectable': [False]*len(geo_name),
                             'Key':key,
                             'Layer Name': [3] * len(geo_name),
                             'LAYER_3_PARENT_PID': parent_key})
exclude_geos

PID                          Display Name  \
0   1296370         South Antelope Valley Exclude   
1   1296371                   Los Angeles Exclude   
2   1296372                       Newhall Exclude   
3   1296373                  Palos Verdes Exclude   
4   1296374           San Fernando Valley Exclude   
5   1296375                Downey-Norwalk Exclude   
6   1296376           Agoura Hills-Malibu Exclude   
7   1296377         North Antelope Valley Exclude   
8   1296378                      Torrance Exclude   
9   1296379                    Long Beach Exclude   
10  1296380                       Compton Exclude   
11  1296381                      Pasadena Exclude   
12  1296382                  Santa Monica Exclude   
13  1296383                      Whittier Exclude   
14  1296384   South Gate-East Los Angeles Exclude   
15  1296385                     Inglewood Exclude   
16  1296386       East San Gabriel Valley Exclude   
17  1296387  Southwest San Gabriel Valley Exclude   
18  1296388      Upper San Gabriel Valley Exclude   
19  1296389              South Bay Cities Exclude   
20  1296390                        Malibu Exclude   
21  1296391                 Santa Clarita Exclude   
22  1296392                       Burbank Exclude   
23  1296393                      Lakewood Exclude   
24  1296394                        Carson Exclude   
25  1296395                      El Monte Exclude   
26  1296396                      Glendale Exclude   

                                             geometry  Selectable  \
0   MULTIPOLYGON (((-118.41935031179692 34.4556713...       False   
1   MULTIPOLYGON (((-118.15562519086262 34.0972612...       False   
2   MULTIPOLYGON (((-118.79916854110421 34.6591309...       False   
3   MULTIPOLYGON (((-118.41752285368544 33.7870119...       False   
4   MULTIPOLYGON (((-118.6512323 34.1222124, -118....       False   
5   MULTIPOLYGON (((-118.0287826347267 33.87332911...       False   
6   MULTIPOLYGON (((-118.8553399004001 34.12746065...       False   
7   MULTIPOLYGON (((-118.87672337092579 34.8032025...       False   
8   MULTIPOLYGON (((-118.37794962358095 33.8528484...       False   
9   MULTIPOLYGON (((-118.061714 33.833639, -118.06...       False   
10  MULTIPOLYGON (((-118.22595622484859 33.9400643...       False   
11  MULTIPOLYGON (((-118.23977087457997 34.2522695...       False   
12                                      POLYGON EMPTY       False   
13  MULTIPOLYGON (((-118.056907 34.010476, -118.05...       False   
14                                      POLYGON EMPTY       False   
15  MULTIPOLYGON (((-118.37005136628527 33.9501476...       False   
16  MULTIPOLYGON (((-117.93030792626816 34.1512972...       False   
17                                      POLYGON EMPTY       False   
18  MULTIPOLYGON (((-118.07723933434065 34.1048957...       False   
19  MULTIPOLYGON (((-118.37507235486426 33.8561856...       False   
20  MULTIPOLYGON (((-118.70341 34.03715, -118.7032...       False   
21                                      POLYGON EMPTY       False   
22                                      POLYGON EMPTY       False   
23                                      POLYGON EMPTY       False   
24                                      POLYGON EMPTY       False   
25                                      POLYGON EMPTY       False   
26                                      POLYGON EMPTY       False   

                                             Key  Layer Name  \
0          South_Antelope_Valley_Exclude_1296371           3   
1                    Los_Angeles_Exclude_1296372           3   
2                        Newhall_Exclude_1296373           3   
3                   Palos_Verdes_Exclude_1296374           3   
4            San_Fernando_Valley_Exclude_1296375           3   
5                 Downey_Norwalk_Exclude_1296376           3   
6            Agoura_Hills_Malibu_Exclude_1296377           3   
7          North_Antelope_Valley_Exclude_1296378           3   
8             

In [18]:
exclude_geos = gpd.GeoDataFrame(exclude_geos, crs='EPSG:4326')
exclude_geos = exclude_geos[(~exclude_geos['geometry'].is_empty) & (exclude_geos['Display Name'] != 'Compton Exclude')]

In [19]:
wrong_type = []
to_drop = []
for g, id in zip(exclude_geos.geometry, exclude_geos['PID']):
    if type(g) == shapely.GeometryCollection:
        wrong_type.append(id)
    elif type(g) in [shapely.LineString, shapely.MultiLineString]:
        to_drop.append(id)
for id in wrong_type:
    poly = []
    for g in exclude_geos.loc[exclude_geos['PID'] == id, 'geometry'].values[0].geoms:
        if type(g) == shapely.geometry.Polygon:
            poly.append(g)
    exclude_geos.loc[exclude_geos['PID'] == id, 'geometry'] = shapely.MultiPolygon(poly)
exclude_geos = exclude_geos[~exclude_geos['Display Name'].isin(to_drop)]
print(wrong_type, to_drop)

[] []


In [20]:
ret_df = pd.concat([layer_3, exclude_geos, layer_2], ignore_index=True)

In [21]:
type(ret_df)

geopandas.geodataframe.GeoDataFrame

In [22]:
ret_df.to_crs('EPSG:4326').to_file('all_layers_la.geojson', driver='GeoJSON')

In [23]:
for index, row in ret_df.iterrows():
    if not type(row['geometry']) in [shapely.Polygon, shapely.MultiPolygon]:
        print(row['Display Name'], type(row['geometry']))

In [24]:
ret_df.head()

Display Name                Key  Selectable   PID LAYER_3_PARENT_PID  \
0    Adams Hill    adams_hill_1187        True  1187              93737   
1     Brockmont     brockmont_1188        True  1188              93737   
2   Chevy Chase   chevy_chase_1189        True  1189              93737   
3  Citrus Grove  citrus_grove_1190        True  1190              93737   
4   City Center   city_center_1191        True  1191              93737   

   Layer Name                                           geometry  
0           3  MULTIPOLYGON (((-118.23777 34.13522, -118.2377...  
1           3  MULTIPOLYGON (((-118.24348 34.17932, -118.2434...  
2           3  MULTIPOLYGON (((-118.19649 34.17991, -118.1964...  
3           3  MULTIPOLYGON (((-118.2288 34.14383, -118.22877...  
4           3  MULTIPOLYGON (((-118.25266 34.15679, -118.2526...

In [25]:
m = folium.Map(location=[34.0549, -118.2426], tiles="CartoDB Positron", zoom_start=9)
folium.GeoJson(exclude_geos, style_function=lambda x: {"fillColor": "red"}, tooltip=folium.GeoJsonTooltip(['Display Name']), name='excludes').add_to(m)
folium.GeoJson(layer_2, style_function=lambda x: {"fillColor": "blue"},tooltip=folium.GeoJsonTooltip(['PID','Display Name']), name='layer2').add_to(m)
folium.GeoJson(layer_3, style_function=lambda x: {"fillColor": "green"},tooltip=folium.GeoJsonTooltip(['Display Name', 'LAYER_3_PARENT_PID']), name='layer3').add_to(m)
folium.LayerControl().add_to(m)
m

In [26]:
ret_df.groupby('PID')['Key'].count().sort_values()

PID
1296369    1
191171     1
191167     1
191166     1
191162     1
          ..
171632     1
171633     1
171635     1
171628     1
998378     1
Name: Key, Length: 545, dtype: int64

In [27]:
check = ret_df[ret_df['Layer Name'] == 2].sjoin(ret_df[ret_df['Layer Name'] == 3], predicate='covers')
check[check['LAYER_3_PARENT_PID_right'] != check['PID_left']]

Empty GeoDataFrame
Columns: [Display Name_left, Key_left, Selectable_left, PID_left, LAYER_3_PARENT_PID_left, Layer Name_left, geometry, index_right, Display Name_right, Key_right, Selectable_right, PID_right, LAYER_3_PARENT_PID_right, Layer Name_right]
Index: []

In [28]:
layer_2[layer_2['PID'] == '90560']

PID Display Name  Selectable            Key  LAYER_3_PARENT_PID  \
10  90560      Compton        True  compton_90560                   1   

                                             geometry  Layer Name  
10  POLYGON ((-118.28303 33.89216, -118.28307 33.8...           2

In [29]:
ret_df.geometry

0      MULTIPOLYGON (((-118.23777 34.13522, -118.2377...
1      MULTIPOLYGON (((-118.24348 34.17932, -118.2434...
2      MULTIPOLYGON (((-118.19649 34.17991, -118.1964...
3      MULTIPOLYGON (((-118.2288 34.14383, -118.22877...
4      MULTIPOLYGON (((-118.25266 34.15679, -118.2526...
                             ...                        
540    POLYGON ((-118.30135 34.15696, -118.30175 34.1...
541    POLYGON ((-118.14586 33.86895, -118.14585 33.8...
542    POLYGON ((-118.29497 33.84634, -118.29482 33.8...
543    POLYGON ((-117.99978 34.08241, -117.99991 34.0...
544    MULTIPOLYGON (((-118.23849 34.26711, -118.2384...
Name: geometry, Length: 545, dtype: geometry

In [30]:
ret_df["geometry"] = [shapely.MultiPolygon([feature]) if isinstance(feature, shapely.Polygon) \

else feature for feature in ret_df["geometry"]]

ret_df.to_crs(crs="EPSG:4326", inplace=True)

In [31]:
layer_2 = ret_df[ret_df['Layer Name'] == 2]
layer_3 = ret_df[ret_df['Layer Name'] == 3]
layer_2.columns = ['Display Name', 'Key', 'Selectable', 'PID', 'LAYER_2_PARENT_PID', 'Layer Name', 'geometry']

In [32]:
layer_3.to_file('data/output/la_layer_3.geojson', driver='GeoJSON')
layer_2.to_file('data/output/la_layer_2.geojson', driver='GeoJSON')

In [ ]:
ret_df[['Display Name', 'Layer Name']].to_clipboard(index=False)